In [2]:
import spacy
import neuralcoref
import pandas as pd
import time
import numpy as np
import re

In [3]:
import sys
sys.version

'3.7.9 (default, Aug 31 2020, 17:10:11) [MSC v.1916 64 bit (AMD64)]'

In [4]:
nlp = spacy.load('en_core_web_md')
neuralcoref.add_to_pipe(nlp)
spacy.__version__

'2.1.0'

In [5]:
def NE_present(comment):
    text = nlp(comment)
    NEs = list(set([e.text for e in text.ents if e.label_ == 'PERSON']))
    if NEs:
        return NEs
    else:
        return False
    

In [87]:
# doc1 = nlp('We, the scouts, are afraid. Alex told us he was upset the other day. The Senator said she wished something could be done about his neuroticisms')
# #print(doc1._.coref_clusters)
# x.text for x in doc1.ents if x.label_ == 'PERSON'

In [6]:
# load data
posts = pd.read_csv("Downloads/2018-01-02_posts.csv", index_col='Unnamed: 0')
cmts = pd.read_csv("Downloads/2018-01-02_comments.csv", index_col='Unnamed: 0')
posts.set_index('id', inplace=True)
cmts.set_index('id', inplace=True)

In [7]:
# only keep comments on collected posts
links = posts.index.unique().tolist()
cmts["link_id"] = cmts["link_id"].str.split("_", n = 1, expand = True)[1] 
df = cmts.query('link_id in @links')

# only keep unique comments
df.drop_duplicates('body', inplace=True)

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  import sys


In [8]:
# Seperate the parent_id comment to determine what the comment is a response to and the id
df["to_type"] = df["parent_id"].str.split("_", n = 1, expand = True)[0] 
df["to_id"] = df["parent_id"].str.split("_", n = 1, expand = True)[1] 
df.drop(columns="parent_id", inplace=True)

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\vanki\anaconda3\envs\NLP\lib\site-packages\pandas\core\frame.py:4312: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFra

In [9]:
# ensure that the to_id, if it's to a post, is addressed to a comment I have in the database!
ids = df.index.unique().tolist()
# drop all comments we do not have the parent/context for. In a while loop so that we always have context
while df[df["to_type"] == "t1"].query("to_id not in @ids").shape[0] > 0:
    df.drop(index=df[df["to_type"] == "t1"].query("to_id not in @ids").index, inplace=True)
    ids = df.index.unique().tolist()

In [10]:
# Process the text -- refer to https://www.reddit.com/r/raerth/comments/cw70q/reddit_comment_formatting/

df.dropna(subset=['body'], inplace=True) # Drop all NaN comments (aka deleted)
# df = df[~df.body == 'removed']
# df = df[~df.body == 'deleted']

# Remove URLs and formatting
df['body'] = df['body'].str.replace(r'\(https?:\/\/.*\)', "URL").str.replace(r'[\[\]]', "")

# Remove all posts from bots
df = df[~df['body'].str.contains(r"I'?( a)?m a bot")] #Generally, bots clearly state they are a bot

# Remove all text formatting (italics / bold)
df['body'] = df['body'].str.replace(r"[_|\*|~|\^|\|]","")
df['body'] = df['body'].str.replace("&lt;","") # drop lists
df['body'] = df['body'].str.replace("&gt;","") # drop quotes?

# Convert all remaining URLs to "URL"
df['body'] = df['body'].str.replace(r'https?:\/\/.*', "URL")

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until
C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:8: FutureWarning: The default value of regex will change from True to False in a future version.
  
C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\vanki\anaconda3\envs\NLP\lib\sit

In [11]:
# Add context to each post
post_reference = posts['title'].to_dict()
post_named = posts['title'].map(NE_present).to_dict()
df['post_named'] = df['link_id'].map(post_named)
df['context'] = df['link_id'].map(post_reference)
# del post_reference

In [12]:
# # If I just want the most recent parent
# df['cmt_context'] = ''
# df['cmt_context'].loc[df[df.to_type == 't1'].index] = df[df.to_type == 't1']['to_id'].map(df['body'].to_dict())

In [13]:
# Add comment context to each comment
references = df[df['to_type']=='t1']['to_id'].to_dict() # Dictionary of child to parent
cmt_reference = df['body'].to_dict() # Comment ID to actual text
def map_keypath(path, refs):
    """ Follows the dictionary path from child to top parent comment. Returns list as a series of strings.
    Feed in the first value as a one element list. Also give the dictioanry of child to parent ID. """
    if path[0] in refs.keys():
        return map_keypath([refs[path[0]]] + path, refs)
    else:
        return '\n'.join(path)

# Create a path of reply-IDs for all comments that reply to comments
df['cmt_context'] = ''
df['cmt_context'].loc[df[df['to_type'] == 't1'].index] = df[df['to_type'] == 't1']['to_id'].map(lambda x: [x]).apply(map_keypath, args=(references,))

C:\Users\vanki\anaconda3\envs\NLP\lib\site-packages\pandas\core\indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [14]:
df = df.sample(100)
df.head()

body  created_utc  \
id                                                                        
ds3esz9  What was aviation safety like in the rest of t...   1514924492   
ds35xhf  Maybe they already tried a test run and though...   1514915378   
ds3jxec  His primary rules were: never allow the public...   1514929736   
ds38wf7  Except that's not what he pleaded guilty to, i...   1514918438   
ds2si6n  I never understood why FCC regulations don't e...   1514897437   

        link_id       created to_type    to_id                  post_named  \
id                                                                           
ds3esz9  7nmrwn  1.514921e+09      t1  ds3ecyf              [Donald Trump]   
ds35xhf  7nnh9o  1.514912e+09      t1  ds357h0  [Franken, Sarah Silverman]   
ds3jxec  7npg7p  1.514926e+09      t1  ds3j05k             [Sarah Sanders]   
ds38wf7  7nnopk  1.514915e+09      t1  ds34d3n                    [Steele]   
ds2si6n  7nlpq4  1.514894e+09      t1  ds2s9cz          [Nixon, John Dean]   

                                                   context  \
id                                                           
ds3esz9  Donald Trump takes credit for zero passenger f...   
ds35xhf  Sarah Silverman defends Franken: Politicians w...   
ds3jxec  Sarah Sanders explains why Trump’s golf addict...   
ds38wf7  Republicans’ Steele dossier conspiracy theory ...   
ds2si6n  John Dean: Nixon ‘Might Have Survived If There...   

                                         cmt_context  
id                                                    
ds3esz9                                      ds3ecyf  
ds35xhf                    ds31tch\nds32gvf\nds357h0  
ds3jxec                    ds3hyqv\nds3isoj\nds3j05k  
ds38wf7                                      ds34d3n  
ds2si6n  ds2q0sq\nds2qry1\nds2r3wp\nds2s4h3\nds2s9cz

In [15]:
t0= time.clock()
df['cmt_named'] = df['body'].map(NE_present)
t1 = time.clock() - t0
print("Time elapsed: ", t1) # CPU seconds elapsed (floating point)

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:1: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  """Entry point for launching an IPython kernel.


Time elapsed:  3.5419740000000104


C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:3: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  This is separate from the ipykernel package so we can avoid doing imports until


In [16]:
df['named'] = df.loc[:,['cmt_named','post_named']].any(axis=1)
#df.drop(columns=['post_named', 'cmt_named'], inplace=True)

In [17]:
# Delete all comments irrelevant to 
i = 0
print("OLD SIZE", df.shape[0])
t0= time.clock()
while i < df.shape[0]:
    if df.cmt_context.iloc[i] == '':
        i += 1
        continue
    context = df.cmt_context.iloc[i].split('\n')
    context = [x for x in context if x in df.index]

    if len(context) > 0:
        if not df.loc[context]['named'].any():
            df.drop(context, inplace=True)
            df.drop(df.index[i], inplace=True)
    i += 1
    
print("NEW SIZE", df.shape[0])
print()
t1 = time.clock() - t0
print("Time elapsed: ", t1) # CPU seconds elapsed (floating point)

OLD SIZE 100
NEW SIZE 100

Time elapsed:  0.003543399999998087


C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:4: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  after removing the cwd from sys.path.
C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:20: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


In [19]:
subset= df

In [25]:
pattern = '|'.join(sorted(re.escape(k) for k in cmt_reference))
pattern

'ds1zd6b|ds1ze5w|ds1zegp|ds1zf9t|ds1zfen|ds1zg51|ds1zji1|ds1zm3o|ds1zm47|ds1zmgo|ds1zmji|ds1znep|ds1znu3|ds1zqmh|ds1zr8p|ds1zs2s|ds1zsvg|ds1zvxj|ds1zwoo|ds1zxji|ds1zxs0|ds1zzd1|ds1zzd8|ds202er|ds202m2|ds204d5|ds204ik|ds2052m|ds205a9|ds205ou|ds205pu|ds2064j|ds206m0|ds208qw|ds209aj|ds20ad8|ds20ane|ds20d45|ds20dd5|ds20ec7|ds20egd|ds20gq7|ds20kax|ds20kec|ds20nnw|ds20o9l|ds20ol1|ds20px4|ds20qaf|ds20qmc|ds20qrm|ds20rmf|ds20s8g|ds20t9f|ds20tw6|ds20vjz|ds20wep|ds20wx7|ds20x1v|ds20xu0|ds20y7t|ds20ygy|ds20yzw|ds211ab|ds213b4|ds213yd|ds2149j|ds214su|ds214we|ds21542|ds215gu|ds215k7|ds216s3|ds216un|ds21794|ds217vy|ds2196z|ds219am|ds219pl|ds21a4u|ds21abl|ds21anj|ds21apb|ds21aqz|ds21ast|ds21avs|ds21c44|ds21cg1|ds21cva|ds21d68|ds21d6t|ds21dc3|ds21dzx|ds21e6u|ds21ev7|ds21f4p|ds21fn8|ds21g2u|ds21g9u|ds21h7u|ds21hvt|ds21hyd|ds21jn3|ds21jvr|ds21k8p|ds21l33|ds21lj0|ds21m8t|ds21mpu|ds21njk|ds21oj9|ds21pg9|ds21pzd|ds21qrq|ds21vi4|ds21z6f|ds21zr7|ds220v9|ds221rj|ds224no|ds224x4|ds226v1|ds226xn|ds227vj|ds228xm

In [20]:

# Create a path of reply-IDs for all comments that reply to comments
subset['cmt_context'] = ''
subset['cmt_context'].loc[subset[subset['to_type'] == 't1'].index] = subset[subset['to_type'] == 't1']['to_id'].map(lambda x: [x]).apply(map_keypath, args=(references,))

# Convert these IDs to the actual text
pattern = '|'.join(sorted(re.escape(k) for k in cmt_reference))
subset['cmt_context'] = subset['cmt_context'].str.replace(pattern, lambda m: cmt_reference.get(m.group(0)), regex=True)

# Merge with post title and drop the not needed column
subset['context'] = subset['context'] + "\n" + df['cmt_context']
subset.drop(columns='cmt_context', inplace=True)

C:\Users\vanki\anaconda3\envs\NLP\lib\site-packages\pandas\core\indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [135]:
# Keep only the most recent parent
subset['direct_parent'] = subset['to_id'].map(cmt_reference)
subset['direct_parent'].loc[subset[subset['to_type'] == 't3'].index] = subset['to_id'].map(post_reference).loc[subset[subset['to_type'] == 't3'].index]

C:\Users\vanki\anaconda3\envs\NLP\lib\site-packages\pandas\core\indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


In [153]:
subset['context'].iloc[0]

"Coal mining deaths skyrocket in 2017\nMaybe killing those safety regulations, wasn't such a good thing afterall?\n\nOh, who am I kidding.  They're perfectly fine with this.  Deaths are up?  Who gives a fuck.  Profits are up!\n\n"

In [155]:
# coreference resolution REQUIRES SPACY 2.1.0
# currently sepearte context from text with lots of whitespace -- see if i can find a better method
subset['test1'] = ''

t0= time.clock()
for i in range(100):
    text = subset['context'].iloc[i] + "\t" + subset['body'].iloc[i]
    doc1 = nlp(text)
    wcontext = doc1._.coref_resolved.rsplit('\t', 1)
    subset['test1'].iloc[i] = wcontext[1] if len(wcontext) > 1 else wcontext #### Sometimes the split doesn't work

#     text = subset['context'].iloc[i] + "\t" + subset['body'].iloc[i]
#     doc1 = nlp(text)
#     wcontext = doc1._.coref_resolved.rsplit('\t', 1)
#     subset['test1'].iloc[i] = wcontext[1] if len(wcontext) > 1 else wcontext #### Sometimes the split doesn't work

t1 = time.clock() - t0
print("Time elapsed: ", t1) # CPU seconds elapsed (floating point)

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:5: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  """


Time elapsed:  49.201249999998254


C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:17: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead


In [159]:
subset['test1'].iloc[74]

"It's not even anarchism, if you mean the political philosophy rather than the colloquial definition. Even anarchists allow for coordination and enforcement of norms amongst groups of likeminded individuals; Even anarchists just don't see the state as a legitimate means of doing this, as the state simply protects entrenched interests and perpetuates inequalities for the benefit of the state own existence. \n\nThe person I'm referring to even considers that to be tyranny. So long as an individual is being prevented from pursuing what an individual want by anything more than another individual doing the same, it's oppression - regardless of what that individual's act or intention is. There's also a morally/ethically nihilist worldview involved in this, where the only thing that can really be proven to independently exist (according to this person, mind) is the individual. It's not solipsism, because they also recognize that obviously other individuals exist, more like a really radical in

In [139]:
for i in range(100):
    print(i)
    print(subset['test4'].iloc[i])
    print('-------------------')

0
Are coal profits up, though? The industry is mortally wounded no matter what Trump does.
-------------------
1
I can already hear the phantom "looks."
-------------------
2
How is laying physical infrastructure, be it roads, telephone lines, or fiber - advocating for corporate welfare? It isn't like saying "Let's subsidize Comcast, lay the line, and beg for them to come." If you build it, various people will come.
-------------------
3
Ah the good times of our long forgotten history (2012) when the 2AM Phone Call was an actual campaign issue and people actually considered how a candidate might handle an actual campaign issue. 
-------------------
4
Oh come on, you exaggerate the all or nothing but. Warren doesn’t have a 13 minute video of Warren lying floating through the front page. Warren was a corrupt candidate plain and simple, we can’t blame the voters for the DNC’s fuck up. 

Warren actually has a bit of bark behind Warren. Warren shortcomings mean nothing in a race against Inc

In [26]:
def resolve(context, body):
    text = context + "\t" + body
    doc1 = nlp(text)
    wcontext = doc1._.coref_resolved.rsplit('\t', 1)
    return wcontext[1] if len(wcontext) > 1 else wcontext #### Sometimes the split doesn't work

In [31]:
t0= time.clock()
subset['test2'] = subset.apply(lambda row: resolve(context = row['context'], body = row['body']), axis=1)
t1 = time.clock() - t0
print("Time elapsed: ", t1) # CPU seconds elapsed (floating point)

C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:1: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  """Entry point for launching an IPython kernel.


Time elapsed:  38.604305600000316


C:\Users\vanki\AppData\Roaming\Python\Python37\site-packages\ipykernel_launcher.py:3: DeprecationWarning: time.clock has been deprecated in Python 3.3 and will be removed from Python 3.8: use time.perf_counter or time.process_time instead
  This is separate from the ipykernel package so we can avoid doing imports until


In [162]:
subset.head

<bound method NDFrame.head of                                                       body  created_utc  \
id                                                                        
ds3a549  Are coal profits up, though? The industry is m...   1514919703   
ds39vtt            I can already hear the phantom "looks."   1514919439   
ds3b8lj  How is laying physical infrastructure, be it r...   1514920825   
ds31xxv  Ah the good times of our long forgotten histor...   1514911134   
ds36psm  Oh come on, you exaggerate the all or nothing ...   1514916190   
...                                                    ...          ...   
ds303wg  And their alternative is? As long as the democ...   1514909022   
ds3culw  65 million votes were cast for democrats in th...   1514922472   
ds3f12i  My favorite King idiocy.URL\n\nDid you know th...   1514924725   
ds35own  Gotta be careful. Liberals are the most danger...   1514915126   
ds2zhz0  The guys has no shoulders. He definitely wears...   151490830

In [163]:
df = subset['test1']

In [164]:
# Save the data for NEL
df.to_csv("processed2.csv")

# Experiment with the data

In [363]:
i = 10149
text = df['context'].iloc[i] + "\t\t\t" + df['body'].iloc[i]
doc1 = nlp(text)
wcontext = doc1._.coref_resolved.rsplit('\t\t\t', 1)
wcontext[1]
doc1._.coref_clusters

[Senate: [Senate, U.S. Senate],
 Former Minnesota Republican U.S. Rep. Michele Bachmann: [Former Minnesota Republican U.S. Rep. Michele Bachmann, her]]

In [318]:
df = df.explode('post_named')
df = df.explode('cmt_named')

In [346]:
df

body  created_utc  \
id                                                                        
ds3nvb2  There was one interview on MSNBC recently wher...   1514933998   
ds3nv9y  I'm ashamed to admit it, but I've never voted ...   1514933996   
ds3nv9y  I'm ashamed to admit it, but I've never voted ...   1514933996   
ds3nv9y  I'm ashamed to admit it, but I've never voted ...   1514933996   
ds3nv9s  And they'll know you're actually okay, and not...   1514933996   
...                                                    ...          ...   
ds1zegp                    This is the Idiocracy timeline.   1514847806   
ds1ze5w                      these celebs need to fuck off   1514847797   
ds1ze5w                      these celebs need to fuck off   1514847797   
ds1zd6b                                 No thank you sir.    1514847766   
ds1zd6b                                 No thank you sir.    1514847766   

        link_id       created to_type    to_id post_named  \
id                                                          
ds3nvb2  7no250  1.514930e+09      t1  ds3ncz8      False   
ds3nv9y  7nmfkw  1.514930e+09      t3   7nmfkw      False   
ds3nv9y  7nmfkw  1.514930e+09      t3   7nmfkw      False   
ds3nv9y  7nmfkw  1.514930e+09      t3   7nmfkw      False   
ds3nv9s  7noa0l  1.514930e+09      t1  ds3mgt8      False   
...         ...           ...     ...      ...        ...   
ds1zegp  7nib4p  1.514844e+09      t3   7nib4p     Dwayne   
ds1ze5w  7nib4p  1.514844e+09      t3   7nib4p    Johnson   
ds1ze5w  7nib4p  1.514844e+09      t3   7nib4p     Dwayne   
ds1zd6b  7nib4p  1.514844e+09      t3   7nib4p    Johnson   
ds1zd6b  7nib4p  1.514844e+09      t3   7nib4p     Dwayne   

                                                   context   cmt_named  named  
id                                                                             
ds3nvb2  Intel Dem: Minority may publish report on ways...       False  False  
ds3nv9y                       2018 Calendar of Primaries\n        Cruz   True  
ds3nv9y                       2018 Calendar of Primaries\n        Beto   True  
ds3nv9y                       2018 Calendar of Primaries\n  Ted Cruz's   True  
ds3nv9s  Here's a Novel Idea: Hold Both Caller and Poli...       False  False  
...                                                    ...         ...    ...  
ds1zegp  Dwayne 'The Rock' Johnson Is 'Seriously Consid...       False   True  
ds1ze5w  Dwayne 'The Rock' Johnson Is 'Seriously Consid...       False   True  
ds1ze5w  Dwayne 'The Rock' Johnson Is 'Seriously Consid...       False   True  
ds1zd6b  Dwayne 'The Rock' Johnson Is 'Seriously Consid...       False   True  
ds1zd6b  Dwayne 'The Rock' Johnson Is 'Seriously Consid...       False   True  

[26607 rows x 10 columns]

In [321]:
import json
with open('politician_data.json') as f:
    wikidata = json.load(f)
    
for i in range(len(wikidata)):
    wikidata[i]['ID'] = i
    
poli_ref = {}
for politician in wikidata:
    poli_ref[politician['name']] = politician['ID']
    if 'givenname' in politician.keys():
        poli_ref[politician['givenname']] = politician['ID']
    if 'familyname' in politician.keys():
        poli_ref[politician['familyname']] = politician['ID']
    if 'nickname' in politician.keys():
        poli_ref[politician['nickname']] = politician['ID']
    if 'pseudonym' in politician.keys():
        poli_ref[politician['pseudonym']] = politician['ID']
        
df['cmt_named'].map(poli_ref) # doesn't work

In [345]:
df.loc['ds3nv9y'].body.iloc[0]

"I'm ashamed to admit it, but I've never voted in a primary election before (November 2016 was my first time to cast a ballot, period).  I have a question:\n\nI think Beto will secure the Democratic nomination (and I plan to vote for him in November), but should I vote in the Republican primary if I think any of Ted Cruz's opponents are less odious than Cruz himself?  Is there anything unethical about that?"

In [221]:
def spacy_entity(df):    
    text = nlp(df)
    df2 = list(set([e.text for e in text.ents if e.label_ == 'PERSON']))
    return df2

#5 secs for 100: 
subset['body'].apply(spacy_entity)

id
ds309jt     [clinton, seth]
ds383k5                  []
ds2ycje       [Hiphopcrisy]
ds3ddor                  []
ds32g4d    [Cryptocurrency]
                 ...       
ds3f8oc                  []
ds31l01    [Obama, Hillary]
ds3nmly       [Obama, Bush]
ds2bdvh                  []
ds2t8ni                  []
Name: body, Length: 100, dtype: object

In [231]:
text = nlp(df.body.loc['ds383k5'])
df2 = list(set([e.text for e in text.ents if e.label_ == 'PERSON']))
if df2:
    print('hi')
else:
    print('no')

no


# Run experiments

In [167]:
subset = df.sample(10000)

In [193]:
for i in range(400,500):
    text = subset['context'].iloc[i] + "\t\t\t" + subset['body'].iloc[i]
    doc1 = nlp(text)
    wcontext = doc1._.coref_resolved.rsplit('\t\t\t', 1)
    

402 7
415 5


In [194]:
subset.context[415]

"Roger Stone retroactively registers lobbying contract\nMany other Trump-connected figures have retroactively registered as lobbyists in recent months, including his former campaign chairman, Paul Manafort, and his former national security adviser Michael Flynn.\n\nOh you mean the guys who were indicted already.  I'm sure that's just a coincidence, right Roger?"

In [16]:
for i,j,n in zip(subset.context,subset.body,range(100)):
    print(n)
    print(i)
    print("TEXT GOES HERE")
    print(j)
    print("--------------------")

0
Tax cuts could make it harder to fight the next recession
I welcome the day. Working class people already have skills, trades and social support networks in place. Wealthy people will have vaults full of worthless paper and shiny metal.
&gt; I welcome the day.

Losing more jobs - of course could not be welcome.

&gt;Working class people already have skills, trades and social support networks in place.

But  were laid off in droves in the last 4 recessions, all as result of tax cuts for the rich.  Millions of factory workers (2001 to 2003) and trades people (2006-2009).


&gt;Wealthy people will have vaults full of worthless paper and shiny metal.

Recession doesn't mean money becomes worthless.  It is true that the wealthy are hurt  by recession - but the donor class doesn't seem to ever think that far ahead.

Income becomes scarce.

But, what is the money worth if the US has no economy anymore?
&gt; But, what is the money worth if the US has no economy anymore?

A completely valid p

In [14]:
i = 1015
text = df['context'].iloc[i] + "||" + df['body'].iloc[i]
doc1 = nlp(text)
doc2 = nlp(df['body'].iloc[i])
print(df['body'].iloc[i])
print()
print()
print("Context:",end=" ")
print(doc1._.coref_resolved.rsplit('||')[1])
print()
print()
# print(doc1._.coref_resolved) # doesn't work very well
print("No context:",end=" ")
print(doc2._.coref_resolved)

How many people died in traffic accidents last year?  Thanks a LOT, Trump.  


Context: How many people died in traffic accidents last year?  Thanks a LOT, Trump.  


No context: How many people died in traffic accidents last year?  Thanks a LOT, Trump.  


In [147]:
df['context'].iloc[8805]

"Warren has raised more campaign money than nearly any senator ever: report\nHillary the Sequel. Good for donors,but doesn't appeal to the Rust Belt.  Even Trump had the good sense to pander to them, and his betrayal of them is an opportunity for Democrats.\nYup.  Not gonna be a popular opinion here, but she's a poison pill in 2020.  She has absolutely ZERO appeal to vast swaths of purple Dems all across the midwest.  I'm not sure I'd even put her on as a VP.  Cabinet member, sure, but her on a presidential ticket is a sure-fire way to lose an election."

In [73]:
# AllenNLP coref resolution
# from allennlp.predictors.predictor import Predictor
# predictor = Predictor.from_path("https://s3-us-west-2.amazonaws.com/allennlp/models/coref-model-2018.02.05.tar.gz")
# needs allennlp version 0.8.3
# from https://github.com/ananyagup/AllenNLP-Coreference-Resolution-in-Python-Readable-clusters
#sent = text # Contains context
sent = text

pred = predictor.predict(
    document= sent
)
clusters = pred['clusters']
document = pred['document']

n = 0
doc = {}
for obj in document:
    doc.update({n :  obj}) #what I'm doing here is creating a dictionary of each word with its respective index, making it easier later.
    n = n+1
    
clus_all = []
cluster = []
clus_one = {}
for i in range(0, len(clusters)):
    one_cl = clusters[i]
    for count in range(0, len(one_cl)):
        obj = one_cl[count]
        for num in range((obj[0]), (obj[1]+1)):
            for n in doc:
                if num == n:
                    cluster.append(doc[n])
    clus_all.append(cluster)
    cluster = [] 
    
print (clus_all) #shows all coreferences 

[['Fox', 'News', 'Fox', 'News', 'Fox', 'News', 'Fox', 'News'], ['Nixon', 'Nixon'], ['John', 'Dean', 'I', 'I', 'my', 'me', 'I'], ['a', 'news', 'organization', 'that', 'pushes', 'provable', 'untruths', 'my', 'wellbeing', 'it', '&', 'gt', 'the', 'Fairness', 'doctrine', 'it'], ['99', '%', 'of', 'scientists', 'them', 'their', 'they'], ['Edit', 'I', 'I', 'Sean', 'Hannity', '’', 'he', 'Keyword', 'Hannity', 'Fairness', 'Rush', 'Limbaugh', 'Breightbart', 'HONEST', '||Can', 'the', 'Fairness', 'Doctrine'], ['news', 'and', 'entertainment', 'them', 'They'], ['America', 'the', 'US'], ['we', 'our'], ['a', 'broadcaster', 'It'], ['ban', 'partisan', 'news', 'radio', 'and', 'TV', 'them'], ['Republicans', 'their'], ['agencies', 'like', 'Fox', ',', 'RT', 'and', 'Breightbart', 'these', 'agencies', 'these', 'agencies'], ['this', 'rule', 'that', 'rule', 'it']]


# Wikidata extraction

In [87]:
import json
#import jsonlines

In [156]:
with open('Downloads/data_politician_2.json') as f:
    wikidata = json.load(f)

In [157]:

# for page in wikidata:
#     for politician in page['results']['bindings']:
#         if politician['sex_or_genderLabel']['value'] == 'male':
#             males.append(politician['politicianLabel']['value'])
#         elif politician['sex_or_genderLabel']['value'] == 'female':
#             females.append(politician['politicianLabel']['value'])
#         else:
#             others.append(politician['politicianLabel']['value'])
wikidata

[{'name': {'ar': 'أولغا ريباكوفا',
   'en': 'Olga Rypakova',
   'es': 'Olga Rypakova',
   'fr': 'Olga Rypakova',
   'hi': 'UNK',
   'ru': 'Рыпакова, Ольга Сергеевна',
   'zh': '奥尔加·雷帕科娃'},
  'gender': 'female',
  'id': 'Q6338'},
 {'name': {'ar': 'UNK',
   'en': 'Olha Saladukha',
   'es': 'Olga Saladukha',
   'fr': 'Olha Saladukha',
   'hi': 'UNK',
   'ru': 'Ольга Валерьевна Саладуха',
   'zh': 'UNK'},
  'gender': 'female',
  'id': 'Q6351'},
 {'name': {'ar': 'UNK',
   'en': 'Remigijus Žemaitaitis',
   'es': 'Remigijus Žemaitaitis',
   'fr': 'Remigijus Žemaitaitis',
   'hi': 'UNK',
   'ru': 'UNK',
   'zh': 'UNK'},
  'gender': 'male',
  'id': 'Q59725'},
 {'name': {'ar': 'UNK',
   'en': 'Marina Weisband',
   'es': 'Marina Weisband',
   'fr': 'Marina Weisband',
   'hi': 'UNK',
   'ru': 'Марина Вайсбанд',
   'zh': 'UNK'},
  'gender': 'female',
  'id': 'Q29315'},
 {'name': {'ar': 'تولسي جابرد',
   'en': 'Tulsi Gabbard',
   'es': 'Tulsi Gabbard',
   'fr': 'Tulsi Gabbard',
   'hi': 'तुलसी गेबार

In [154]:
wikidata

[{'head': {'vars': ['politician',
    'sex_or_gender',
    'politicianLabel',
    'sex_or_genderLabel']},
  'results': {'bindings': [{'politician': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q10218'},
     'sex_or_gender': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q6581097'},
     'politicianLabel': {'xml:lang': 'en',
      'type': 'literal',
      'value': 'Rahul Gandhi'},
     'sex_or_genderLabel': {'xml:lang': 'en',
      'type': 'literal',
      'value': 'male'}},
    {'politician': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q10694'},
     'sex_or_gender': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q6581072'},
     'politicianLabel': {'xml:lang': 'en',
      'type': 'literal',
      'value': 'Leanne Wood'},
     'sex_or_genderLabel': {'xml:lang': 'en',
      'type': 'literal',
      'value': 'female'}},
    {'politician': {'type': 'uri',
      'value': 'http://www.wikidata.org/entity/Q11668'},
     'se

In [104]:
males = []
females = []
others = []

for politician in wikidata:
    if politician['gender'] == 'male':
        males.append(politician['name']['en'])
    elif politician['gender'] == 'female':
        females.append(politician['name']['en'])
    else:
        others.append(politician['name']['en'])

diverse Terry Reintke
diverse Alexander Alvina Chamberland
diverse Michelle Suárez Bértora
diverse Yollada Suanyot
diverse Leo Kret
diverse Diane Marie Rodriguez Zambrano
diverse Danica Roem
diverse Phillipe Cunningham
diverse Alessandra Ramos Makkeda
diverse Bhumika Shrestha
diverse Erica Malunguinho
diverse Ida Damgaard
diverse Duda Salabert
diverse Olave Nduwanje
diverse Mauree Turner
diverse Anna Grodzka
diverse Micheline Montreuil
diverse Kellie Maloney
diverse Tamara Adrián
diverse Nora Greenberg
diverse Cacareco
diverse Dana Beyer
diverse Corine van Dun
diverse Georgina Beyer
diverse Carla Antonelli
diverse Jamie Lee Hamilton
diverse Andrea Jenkins
diverse Jess Herbst
diverse Christine Hallquist
diverse Rachel Levine
diverse Camille Cabral
diverse Marcella Di Folco
diverse Leslie Feinberg
diverse Stu Rasmussen
diverse Rose Venkatesan
diverse Annunziata Rees-Mogg
diverse Jowelle de Souza
diverse Tony Briffa
diverse Tessa Ganserer
diverse Alia Dannenberg
diverse Paulien De Groote


In [116]:
female_firstnames = [i.split(' ')[0] for i in females]
female_lastnames = [i.split(' ',1)[1] for i in females if len(i.split(' ')) > 1] 
male_firstnames = [i.split(' ')[0] for i in males]
male_lastnames = [i.split(' ',1)[1] for i in males if len(i.split(' ')) > 1] 
others_lastnames = [i.split(' ',1)[1] for i in others if len(i.split(' ')) > 1] 

In [117]:
female_ln = set(female_lastnames).difference(set(male_lastnames)).difference(set(others_lastnames))
male_ln = set(male_lastnames).difference(set(female_lastnames)).difference(set(others_lastnames))
others_ln = set(others_lastnames).difference(set(female_lastnames)).difference(set(male_lastnames))

In [118]:
female_fn = set(female_firstnames).difference(set(male_firstnames))
male_fn = set(male_firstnames).difference(set(female_firstnames))

In [123]:
# I may need to hand make nicknames based off the data
female_nn = ['AOC']
male_nn = []

False